In [1]:
!nvidia-smi

Wed May 29 06:09:00 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.129.03             Driver Version: 535.129.03   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla P100-PCIE-16GB           Off | 00000000:00:04.0 Off |                    0 |
| N/A   37C    P0              26W / 250W |      0MiB / 16384MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [2]:

!pip install diffusers transformers torch torchaudio gradio pydub

  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 42.4 MB/s eta 0:00:0000:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.3/12.3 MB 86.8 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 315.9/315.9 kB 13.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.8/8.8 MB 95.0 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.2/47.2 kB 3.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.1/121.1 kB 9.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 129.9/129.9 kB 8.3 MB/s eta 0:00:00
  Created wheel for ffmpy: filename=ffmpy-0.3.2-py3-none-any.whl size=5584 sha256=07d8b5ca36f59858de11721ee709053a27dded519e1d8c9c45aa6aefc2be48de
  Stored in directory: /root/.cache/pip/wheels/bd/65/9a/671fc6dcde07d4418df0c592f8df512b26d7a0029c2a23dd81
Successfully built ffmpy
  Attempting uninstall: websockets
    Found existing installation: websockets 12.0
    Uninstalling 

In [3]:
from diffusers import DiffusionPipeline
from PIL import Image
from io import BytesIO  # Added import
from scipy.io import wavfile
import numpy as np
from pydub import AudioSegment
import torch
import torchaudio
import typing as T



The cache for model files in Transformers v4.22.0 has been updated. Migrating your old cache. This is a one-time only operation. You can interrupt this and resume the migration later on by calling `transformers.utils.move_cache()`.


0it [00:00, ?it/s]

2024-05-29 06:09:31.041307: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-05-29 06:09:31.041402: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-05-29 06:09:31.173034: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [4]:
from IPython.display import Audio

# Helper function for spectogram to audio and vice versa:

In [5]:

# Provided functions for audio processing
def waveform_from_spectrogram(
    Sxx: np.ndarray,
    n_fft: int,
    hop_length: int,
    win_length: int,
    num_samples: int,
    sample_rate: int,
    mel_scale: bool = True,
    n_mels: int = 512,
    num_griffin_lim_iters: int = 32,
    device: str = "cuda:0",
) -> np.ndarray:
    """
    Reconstruct a waveform from a spectrogram.

    This is an approximate inverse of spectrogram_from_waveform, using the Griffin-Lim algorithm
    to approximate the phase.
    """
    Sxx_torch = torch.from_numpy(Sxx).to(device)

    # TODO: Make this a class that caches the two things

    if mel_scale:
        mel_inv_scaler = torchaudio.transforms.InverseMelScale(
            n_mels=n_mels,
            sample_rate=sample_rate,
            f_min=0,
            f_max=10000,
            n_stft=n_fft // 2 + 1,
            norm=None,
            mel_scale="htk"
        ).to(device)

        Sxx_torch = mel_inv_scaler(Sxx_torch)

    griffin_lim = torchaudio.transforms.GriffinLim(
        n_fft=n_fft,
        win_length=win_length,
        hop_length=hop_length,
        power=1.0,
        n_iter=num_griffin_lim_iters,
    ).to(device)

    waveform = griffin_lim(Sxx_torch).cpu().numpy()

    return waveform

def audio_from_spectrogram_image(image: Image.Image) -> T.Tuple[BytesIO, float]:  # Modified return type
    """
    Reconstruct a WAV audio clip from a spectrogram image. Also returns the duration in seconds.
    """
    max_volume = 50
    power_for_image = 0.25
    Sxx = spectrogram_from_image(image, max_volume=max_volume, power_for_image=power_for_image)

    sample_rate = 44100  # [Hz]
    clip_duration_ms = 5000  # [ms]

    bins_per_image = 512
    n_mels = 512

    # FFT parameters
    window_duration_ms = 100  # [ms]
    padded_duration_ms = 400  # [ms]
    step_size_ms = 10  # [ms]

    # Derived parameters
    num_samples = int(image.width / float(bins_per_image) * clip_duration_ms) * sample_rate
    n_fft = int(padded_duration_ms / 1000.0 * sample_rate)
    hop_length = int(step_size_ms / 1000.0 * sample_rate)
    win_length = int(window_duration_ms / 1000.0 * sample_rate)

    samples = waveform_from_spectrogram(
        Sxx=Sxx,
        n_fft=n_fft,
        hop_length=hop_length,
        win_length=win_length,
        num_samples=num_samples,
        sample_rate=sample_rate,
        mel_scale=True,
        n_mels=n_mels,
        num_griffin_lim_iters=32,
    )

    wav_bytes = BytesIO()  # Changed from io.BytesIO()
    wavfile.write(wav_bytes, sample_rate, samples.astype(np.int16))
    wav_bytes.seek(0)

    duration_s = float(len(samples)) / sample_rate

    return wav_bytes, duration_s

def spectrogram_from_image(
    image: Image.Image, max_volume: float = 50, power_for_image: float = 0.25
) -> np.ndarray:
    """
    Compute a spectrogram magnitude array from a spectrogram image.

    TODO: Add image_from_spectrogram and call this out as the reverse.
    """
    # Convert to a numpy array of floats
    data = np.array(image).astype(np.float32)

    # Flip Y take a single channel
    data = data[::-1, :, 0]

    # Invert
    data = 255 - data

    # Rescale to max volume
    data = data * max_volume / 255

    # Reverse the power curve
    data = np.power(data, 1 / power_for_image)

    return data

# Creating riffusion pipeline:

In [6]:



# function to load the riffusion model into stable diffusion pipeline

pipe = DiffusionPipeline.from_pretrained("riffusion/riffusion-model-v1")
pipe = pipe.to("cuda")





model_index.json:   0%|          | 0.00/541 [00:00<?, ?B/s]

unet/diffusion_pytorch_model.safetensors not found


Fetching 15 files:   0%|          | 0/15 [00:00<?, ?it/s]

safety_checker/pytorch_model.bin:   0%|          | 0.00/1.22G [00:00<?, ?B/s]

scheduler/scheduler_config.json:   0%|          | 0.00/284 [00:00<?, ?B/s]

...

unet/config.json:   0%|          | 0.00/743 [00:00<?, ?B/s]

tokenizer/vocab.json:   0%|          | 0.00/1.06M [00:00<?, ?B/s]

vae/diffusion_pytorch_model.bin:   0%|          | 0.00/335M [00:00<?, ?B/s]

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

/opt/conda/lib/python3.10/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
/opt/conda/lib/python3.10/site-packages/diffusers/pipelines/stable_diffusion/pipeline_stable_diffusion.py:251: FutureWarning: The configuration file of the unet has set the default `sample_size` to smaller than 64 which seems highly unlikely. If your checkpoint is a fine-tuned version of any of the following: 
- CompVis/stable-diffusion-v1-4 
- CompVis/stable-diffusion-v1-3 
- CompVis/stable-diffusion-v1-2 
- CompVis/stable-diffusion-v1-1 
- runwayml/stable-diffusion-v1-5 
- runwayml/stable-diffusion-inpainting 
 you should change 'sample_size' to 64 in the configuration file. Please make sure to upda

In [7]:
# function to generate melody using pipeline:

def predict(prompt, negative_prompt):
    spec = pipe(
        prompt,
        negative_prompt=negative_prompt,
        width=768,
    ).images[0]
    
    wav_bytes, duration_s = audio_from_spectrogram_image(spec)
    wav_bytes.seek(0)
    return wav_bytes, spec


# Generation using pretrained riffusion:

In [8]:
# generation 1

prompt = "solo piano piece, classical"
negative_prompt = "drums"

wav_bytes, spec = predict(prompt, negative_prompt)

audio = AudioSegment.from_file(wav_bytes, format="wav")
audio.export('output.wav', format='wav')
Audio('output.wav')

  0%|          | 0/50 [00:00<?, ?it/s]

In [9]:
# generation 2

prompt = "jazz music with a mood. Whistle sprinting comical song comical, piano solo"
negative_prompt = "low quality"

wav_bytes, spec = predict(prompt, negative_prompt)

audio = AudioSegment.from_file(wav_bytes, format="wav")
audio.export('output.wav', format='wav')
Audio('output.wav')


  0%|          | 0/50 [00:00<?, ?it/s]

In [10]:
# generation 3

prompt = "Electro piano trio with a sense of speed"
negative_prompt = "piano"

wav_bytes, spec = predict(prompt, negative_prompt)

audio = AudioSegment.from_file(wav_bytes, format="wav")
audio.export('output.wav', format='wav')
Audio('output.wav')


  0%|          | 0/50 [00:00<?, ?it/s]

# Fine-tuning on custom blues dataset:

In [11]:
import os
from PIL import Image
from torch.utils.data import Dataset, DataLoader
from torchvision import transforms
from diffusers import DiffusionPipeline, UNet2DConditionModel
from diffusers.optimization import get_scheduler
import torch
from torch.optim import AdamW
from tqdm import tqdm

# Define the dataset class
class SpectrogramDataset(Dataset):
    def __init__(self, image_folder, prompt, transform=None):
        self.image_folder = image_folder
        self.prompt = prompt
        self.transform = transform
        self.image_files = [f for f in os.listdir(image_folder) if f.endswith('.png') or f.endswith('.jpg')]

    def __len__(self):
        return len(self.image_files)

    def __getitem__(self, idx):
        img_name = os.path.join(self.image_folder, self.image_files[idx])
        image = Image.open(img_name).convert('RGB')
        if self.transform:
            image = self.transform(image)
        return {'image': image, 'prompt': self.prompt}

# Define transformations for the images
transform = transforms.Compose([
    transforms.Resize((512, 512)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.5, 0.5, 0.5], std=[0.5, 0.5, 0.5])
])

# Create the dataset and data loader
image_folder = '/kaggle/input/imgdata/blues'
prompt = 'blues'
dataset = SpectrogramDataset(image_folder, prompt, transform=transform)
dataloader = DataLoader(dataset, batch_size=4, shuffle=True, num_workers=2)

# Load the pre-trained pipeline
pipe = DiffusionPipeline.from_pretrained("riffusion/riffusion-model-v1", torch_dtype=torch.float16)
pipe = pipe.to("cuda")

# Prepare the model for training
model = pipe.unet
model.train()

# Set up the optimizer and learning rate scheduler
optimizer = AdamW(model.parameters(), lr=5e-5)
scheduler = get_scheduler(
    name="linear",
    optimizer=optimizer,
    num_warmup_steps=0,
    num_training_steps=len(dataloader) * 5  # Example for 5 epochs
)
# Training loop
epochs = 5
device = "cuda"
for epoch in range(epochs):
    for batch in tqdm(dataloader, desc=f"Epoch {epoch+1}/{epochs}"):
        # Move data to device
        images = batch['image'].to(device)
        prompt = str(batch['prompt'])  # Retrieve prompt for this batch
        prompts = [prompt] * len(images)  # Ensuring prompt is a list of strings

        # Generate noise and add it to the images
        noise = torch.randn_like(images).to(device)
        noisy_images = images + noise
        
        # Prepare the inputs for the pipeline
        inputs = {"prompt": prompts, "negative_prompt": None, "images": noisy_images}

        # Perform forward pass using the pipeline
        optimizer.zero_grad()
        try:
            outputs = pipe(**inputs)
        except TypeError:
            # If the pipeline expects prompt as a single string, convert it
            inputs["prompt"] = [prompt]  # Convert prompt to list of single string
            outputs = pipe(**inputs)

        # Access the generated images
        generated_images = outputs.images
        
        # Convert PIL images to tensors
        generated_images = torch.stack([transforms.ToTensor()(img).to(device) for img in generated_images])

        # Detach the generated_images from the computational graph
        generated_images = generated_images.detach().requires_grad_()
        
        # Compute the loss (assuming L2 loss for simplicity)
        loss = torch.nn.functional.mse_loss(generated_images, images)
        
        # Perform backward pass and optimization step
        loss.backward()
        optimizer.step()
        scheduler.step()
    
    print(f"Epoch {epoch+1}/{epochs}, Loss: {loss.item()}")

# Save the fine-tuned model
pipe.save_pretrained("fine-tuned-riffusion-model")



unet/diffusion_pytorch_model.safetensors not found


Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

Epoch 1/5:   0%|          | 0/25 [00:00<?, ?it/s]

  0%|          | 0/50 [00:00<?, ?it/s]

Epoch 1/5:   4%|▍         | 1/25 [00:47<19:03, 47.65s/it]

...

  0%|          | 0/50 [00:00<?, ?it/s]

Epoch 5/5:  96%|█████████▌| 24/25 [18:54<00:47, 47.24s/it]

  0%|          | 0/50 [00:00<?, ?it/s]

Epoch 5/5: 100%|██████████| 25/25 [19:41<00:00, 47.26s/it]


Epoch 5/5, Loss: 1.2157654762268066


In [15]:
import torch
from diffusers import DiffusionPipeline

# Load the fine-tuned model
fine_tuned_model_path = "fine-tuned-riffusion-model"
pipe3 = DiffusionPipeline.from_pretrained(fine_tuned_model_path)
pipe3 = pipe3.to("cuda")

Loading pipeline components...:   0%|          | 0/7 [00:00<?, ?it/s]

### We can change the width of generated spectrograms for longer audio file generation. 

Note: But, in longer generation the flow may break as the pipeline is trained mainly to generate files of atmost 7-8 seconds.

In [25]:
# function to generate melody from fine-tuned model:

#width = 768
def predict2(prompt, negative_prompt):
    spec = pipe3(
        prompt,
        negative_prompt=negative_prompt,
        width=1008,
        num_inference_steps=200
    ).images[0]
    
    wav_bytes, duration_s = audio_from_spectrogram_image(spec)
    wav_bytes.seek(0)
    return wav_bytes, spec



# Test prompts samples:

In [22]:
# melody generation 1 using fine-tuned model 

prompt = "blues ,solo piano piece, classical"
negative_prompt = "drums"

wav_bytes, spec = predict2(prompt, negative_prompt)

audio = AudioSegment.from_file(wav_bytes, format="wav")
audio.export('output.wav', format='wav')
Audio('output.wav')


  0%|          | 0/100 [00:00<?, ?it/s]

In [26]:
# melody generation 2 using fine-tuned model

prompt = "blues ,pop with drums,melodic"
negative_prompt = "piano"

wav_bytes, spec = predict2(prompt, negative_prompt)

audio = AudioSegment.from_file(wav_bytes, format="wav")
audio.export('output.wav', format='wav')
Audio('output.wav')


  0%|          | 0/200 [00:00<?, ?it/s]